In [1]:
# Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
# Set output folder:
BASE_DIR = "/content/drive/MyDrive/Pipeline_CryptoCoin"
DATA_DIR = f"{BASE_DIR}/data"
OUT_DIR  = f"{BASE_DIR}/outputs"

In [3]:
# Install + Setup Spark on Colab

!pip -q install pyspark datasets

In [4]:
# Create Spark session (more stable than defaults):
import os
from pyspark.sql import SparkSession

spark = (SparkSession.builder
    .appName("CryptoCoin_Regression_Colab")
    .config("spark.driver.memory", "8g")
    .config("spark.executor.memory", "4g")
    .config("spark.sql.shuffle.partitions", "200")
    .config("spark.memory.offHeap.enabled", "true")
    .config("spark.memory.offHeap.size", "2g")
    .getOrCreate()
)

spark.sparkContext.setLogLevel("WARN")

In [5]:
# Load dataset

from datasets import load_dataset

ds = load_dataset("linxy/CryptoCoin")
train_ds = ds["train"]

# Shuffle then select 150k rows (fast, reproducible)
train_150k = train_ds.shuffle(seed=42).select(range(150_000))

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/450 [00:00<?, ?it/s]

1INCHUSDT_30m.csv:   0%|          | 0.00/10.6M [00:00<?, ?B/s]

1INCHUSDT_1d.csv:   0%|          | 0.00/219k [00:00<?, ?B/s]

...

ZRXUSDT_4h.csv:   0%|          | 0.00/1.87M [00:00<?, ?B/s]

ZRXUSDT_5m.csv:   0%|          | 0.00/81.5M [00:00<?, ?B/s]

ZRXUSDT_6h.csv:   0%|          | 0.00/1.25M [00:00<?, ?B/s]

ZRXUSDT_8h.csv:   0%|          | 0.00/946k [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [6]:
# Convert to pandas then Spark
import pandas as pd

pdf = train_150k.to_pandas()
print(pdf.shape)
pdf.head(3)

(150000, 12)


Open time      open      high       low     close     volume  \
0  2022-07-25 21:45:00   0.03820   0.03820   0.03812   0.03816  290341.80   
1  2021-01-05 23:25:00   0.02031   0.02037   0.02028   0.02036   27689.60   
2  2021-06-23 01:45:00  11.31600  11.40000  11.30600  11.32000    7740.11   

                Close time  Quote asset volume  Number of trades  \
0  2022-07-25 21:49:59.999        11077.801137                59   
1  2021-01-05 23:29:59.999          563.252330                18   
2  2021-06-23 01:49:59.999        87932.907150               269   

   Taker buy base asset volume  Taker buy quote asset volume  Ignore  
0                    41836.600                   1596.475769       0  
1                     6610.200                    134.402979       0  
2                     4778.637                  54312.417792       0

In [7]:
# Basic cleanup (ensure numeric columns are numeric):

numeric_cols = [
    "open","high","low","close","volume",
    "Quote asset volume",
    "Number of trades",
    "Taker buy base asset volume",
    "Taker buy quote asset volume",
    "Ignore"
]

for c in numeric_cols:
    if c in pdf.columns:
        pdf[c] = pd.to_numeric(pdf[c], errors="coerce")

# Parse timestamps
pdf["Open time"] = pd.to_datetime(pdf["Open time"], errors="coerce")
pdf["Close time"] = pd.to_datetime(pdf["Close time"], errors="coerce")

pdf = pdf.dropna(subset=["Open time","close"])  # minimum required
pdf = pdf.sort_values("Open time").reset_index(drop=True)

In [8]:
# Create Spark DataFrame:

sdf = spark.createDataFrame(pdf)

In [9]:
# Save the dataset to Drive as CSV


os.makedirs(DATA_DIR, exist_ok=True)

sample_csv_path = f"{DATA_DIR}/cryptocoin_150k_sample.csv"
pdf.to_csv(sample_csv_path, index=False)
print("Saved:", sample_csv_path)

Saved: /content/drive/MyDrive/Pipeline_CryptoCoin/data/cryptocoin_150k_sample.csv


In [10]:
# Build a Regression Target

from pyspark.sql import functions as F
from pyspark.sql.window import Window

w = Window.orderBy(F.col("Open time").asc())

sdf2 = (sdf
    .withColumn("close_next", F.lead(F.col("close"), 1).over(w))
    .withColumn("label", F.log(F.col("close_next")) - F.log(F.col("close")))
    .dropna(subset=["close_next", "label"])
)

In [11]:
# Feature Engineering
sdf2 = (sdf2
    .withColumn("range", F.col("high") - F.col("low"))
    .withColumn("body", F.col("close") - F.col("open"))
    .withColumn("log_volume", F.log1p(F.col("volume")))
    .withColumn("buy_pressure",
                F.when(F.col("volume") > 0, F.col("Taker buy base asset volume") / F.col("volume"))
                 .otherwise(F.lit(0.0)))
    .withColumn("hlc3", (F.col("high") + F.col("low") + F.col("close")) / F.lit(3.0))
)

In [12]:
feature_cols = [
    "open","high","low","close",
    "volume","log_volume",
    "Quote asset volume",
    "Number of trades",
    "Taker buy base asset volume",
    "Taker buy quote asset volume",
    "range","body","buy_pressure","hlc3"
]

existing = set(sdf2.columns)
feature_cols = [c for c in feature_cols if c in existing]
print("Using features:", feature_cols)

Using features: ['open', 'high', 'low', 'close', 'volume', 'log_volume', 'Quote asset volume', 'Number of trades', 'Taker buy base asset volume', 'Taker buy quote asset volume', 'range', 'body', 'buy_pressure', 'hlc3']


In [13]:
# Create a numeric time index and split by quantiles (approx temporal split)
sdf2 = sdf2.withColumn("ts", F.col("Open time").cast("timestamp").cast("long"))

# Get split thresholds
qs = sdf2.approxQuantile("ts", [0.8, 0.9], 0.01)
t80, t90 = qs[0], qs[1]

train_df = sdf2.filter(F.col("ts") <= t80)
val_df   = sdf2.filter((F.col("ts") > t80) & (F.col("ts") <= t90))
test_df  = sdf2.filter(F.col("ts") > t90)

print(train_df.count(), val_df.count(), test_df.count())

118638 14569 16461


In [14]:
# Cache (helps training speed):
train_df = train_df.cache()
val_df   = val_df.cache()
test_df  = test_df.cache()

In [18]:
# Train Regression Models (MLlib)
from pyspark.ml import Pipeline
from pyspark.ml.feature import VectorAssembler, StandardScaler
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql import functions as F
import os, pandas as pd

os.makedirs(OUT_DIR, exist_ok=True)

assembler = VectorAssembler(inputCols=feature_cols, outputCol="features_raw", handleInvalid="skip")
scaler = StandardScaler(inputCol="features_raw", outputCol="features", withMean=True, withStd=True)

rmse_eval = RegressionEvaluator(labelCol="label", predictionCol="prediction", metricName="rmse")
mae_eval  = RegressionEvaluator(labelCol="label", predictionCol="prediction", metricName="mae")
r2_eval   = RegressionEvaluator(labelCol="label", predictionCol="prediction", metricName="r2")

results = []

In [19]:
def make_export_df(pred_full):
    return pred_full.select(
        F.col("Open time").alias("open_time"),
        "open","high","low","close","volume",
        F.col("label").alias("y_true"),
        F.col("prediction").alias("y_pred")
    )

In [20]:
# Model 1 — Linear Regression
from pyspark.ml.regression import LinearRegression

lr = LinearRegression(featuresCol="features", labelCol="label", maxIter=50, regParam=0.01, elasticNetParam=0.0)
lr_pipe = Pipeline(stages=[assembler, scaler, lr])
lr_model = lr_pipe.fit(train_df)

lr_pred_full = lr_model.transform(test_df)  # contains 'prediction'
lr_rmse = rmse_eval.evaluate(lr_pred_full)
lr_mae  = mae_eval.evaluate(lr_pred_full)
lr_r2   = r2_eval.evaluate(lr_pred_full)

print("LinearRegression -> RMSE:", lr_rmse, " MAE:", lr_mae, " R2:", lr_r2)
results.append({"model": "LinearRegression", "rmse": float(lr_rmse), "mae": float(lr_mae), "r2": float(lr_r2)})

lr_export = make_export_df(lr_pred_full)
lr_out_dir = f"{OUT_DIR}/predictions_LinearRegression"
lr_export.coalesce(1).write.mode("overwrite").option("header", True).csv(lr_out_dir)

LinearRegression -> RMSE: 4.845778573709865  MAE: 3.649513680435972  R2: 0.2802276456850975


In [21]:
# Model 2 — Decision Tree Regressor

from pyspark.ml.regression import DecisionTreeRegressor

dt = DecisionTreeRegressor(featuresCol="features", labelCol="label", maxDepth=10)
dt_pipe = Pipeline(stages=[assembler, scaler, dt])
dt_model = dt_pipe.fit(train_df)

dt_pred_full = dt_model.transform(test_df)
dt_rmse = rmse_eval.evaluate(dt_pred_full)
dt_mae  = mae_eval.evaluate(dt_pred_full)
dt_r2   = r2_eval.evaluate(dt_pred_full)

print("DecisionTree -> RMSE:", dt_rmse, " MAE:", dt_mae, " R2:", dt_r2)
results.append({"model": "DecisionTree", "rmse": float(dt_rmse), "mae": float(dt_mae), "r2": float(dt_r2)})

dt_export = make_export_df(dt_pred_full)
dt_out_dir = f"{OUT_DIR}/predictions_DecisionTree"
dt_export.coalesce(1).write.mode("overwrite").option("header", True).csv(dt_out_dir)

DecisionTree -> RMSE: 4.179604573445297  MAE: 3.170131361075249  R2: 0.46452595780834227


In [22]:
# Model 3 — Random Forest Regressor

from pyspark.ml.regression import RandomForestRegressor

rf = RandomForestRegressor(
    featuresCol="features", labelCol="label",
    numTrees=100, maxDepth=12,
    featureSubsetStrategy="auto",
    seed=42
)

rf_pipe = Pipeline(stages=[assembler, scaler, rf])
rf_model = rf_pipe.fit(train_df)

rf_pred_full = rf_model.transform(test_df)
rf_rmse = rmse_eval.evaluate(rf_pred_full)
rf_mae  = mae_eval.evaluate(rf_pred_full)
rf_r2   = r2_eval.evaluate(rf_pred_full)

print("RandomForest -> RMSE:", rf_rmse, " MAE:", rf_mae, " R2:", rf_r2)
results.append({"model": "RandomForest", "rmse": float(rf_rmse), "mae": float(rf_mae), "r2": float(rf_r2)})

rf_export = make_export_df(rf_pred_full)
rf_out_dir = f"{OUT_DIR}/predictions_RandomForest"
rf_export.coalesce(1).write.mode("overwrite").option("header", True).csv(rf_out_dir)

RandomForest -> RMSE: 4.103424453857856  MAE: 3.1216896082374115  R2: 0.4838678458293001


In [23]:
# Model 4 — Gradient-Boosted Trees Regressor

from pyspark.ml.regression import GBTRegressor

gbt = GBTRegressor(featuresCol="features", labelCol="label", maxIter=50, maxDepth=6, seed=42)
gbt_pipe = Pipeline(stages=[assembler, scaler, gbt])
gbt_model = gbt_pipe.fit(train_df)

gbt_pred_full = gbt_model.transform(test_df)
gbt_rmse = rmse_eval.evaluate(gbt_pred_full)
gbt_mae  = mae_eval.evaluate(gbt_pred_full)
gbt_r2   = r2_eval.evaluate(gbt_pred_full)

print("GBTRegressor -> RMSE:", gbt_rmse, " MAE:", gbt_mae, " R2:", gbt_r2)
results.append({"model": "GBTRegressor", "rmse": float(gbt_rmse), "mae": float(gbt_mae), "r2": float(gbt_r2)})

gbt_export = make_export_df(gbt_pred_full)
gbt_out_dir = f"{OUT_DIR}/predictions_GBTRegressor"
gbt_export.coalesce(1).write.mode("overwrite").option("header", True).csv(gbt_out_dir)

GBTRegressor -> RMSE: 4.121378245725356  MAE: 3.1244532264607714  R2: 0.4793414794305364


In [24]:
# Save All Model Metrics to One CSV

perf_pdf = pd.DataFrame(results).sort_values("rmse")
perf_path = f"{OUT_DIR}/model_performance.csv"
perf_pdf.to_csv(perf_path, index=False)
print("Saved:", perf_path)
perf_pdf

Saved: /content/drive/MyDrive/Pipeline_CryptoCoin/outputs/model_performance.csv


model      rmse       mae        r2
2      RandomForest  4.103424  3.121690  0.483868
3      GBTRegressor  4.121378  3.124453  0.479341
1      DecisionTree  4.179605  3.170131  0.464526
0  LinearRegression  4.845779  3.649514  0.280228

In [25]:
# Convert Spark “folder CSV” to single CSV file
import glob, shutil

def spark_csv_folder_to_single_file(folder_path: str, out_file: str):
    part_files = glob.glob(os.path.join(folder_path, "part-*.csv"))
    if not part_files:
        raise FileNotFoundError(f"No part files found in {folder_path}")
    shutil.copy(part_files[0], out_file)
    print("Single CSV saved:", out_file)

spark_csv_folder_to_single_file(lr_out_dir,  f"{OUT_DIR}/predictions_LinearRegression.csv")
spark_csv_folder_to_single_file(dt_out_dir,  f"{OUT_DIR}/predictions_DecisionTree.csv")
spark_csv_folder_to_single_file(rf_out_dir,  f"{OUT_DIR}/predictions_RandomForest.csv")
spark_csv_folder_to_single_file(gbt_out_dir, f"{OUT_DIR}/predictions_GBTRegressor.csv")

Single CSV saved: /content/drive/MyDrive/Pipeline_CryptoCoin/outputs/predictions_LinearRegression.csv
Single CSV saved: /content/drive/MyDrive/Pipeline_CryptoCoin/outputs/predictions_DecisionTree.csv
Single CSV saved: /content/drive/MyDrive/Pipeline_CryptoCoin/outputs/predictions_RandomForest.csv
Single CSV saved: /content/drive/MyDrive/Pipeline_CryptoCoin/outputs/predictions_GBTRegressor.csv
